# Generate word2vec model - include all new topic words

In [1]:
from gensim.models import Word2Vec, KeyedVectors
import gensim
import time
import numpy as np
from tqdm import tqdm
from pprint import pprint
import pickle
import spacy
import re
import operator
import spacy_udpipe

In [2]:
nlp = spacy.load('el_core_news_sm')

In [3]:
# set variables 
LANG = 'el'
MAX_WORDS = 500000  # maximum processed words to small model 

MODEL_DIR = '/mnt/data/data/models-fasttext/'
TOPICS_DIR = '/home/dzon/kajo/topics/topic_lists-based_on_en-US/'

model_filename = MODEL_DIR + 'cc.'+ LANG +'.300-lemma_500k_min2.vec.bin'

excluded_model_name = MODEL_DIR + 'cc.'+ LANG +'.300-lemma_500k_min2_excluded.vec.bin'

model_orig_filename = MODEL_DIR + 'cc.'+ LANG +'.300.vec.bin'
model_orig_filename_vec = MODEL_DIR + 'cc.'+ LANG +'.300.vec.gz'

pickled_words_lemmas = MODEL_DIR + LANG + '_ft_all_words_lemmas.pickle'

lemma_list_file = TOPICS_DIR + 'topics_lemma_'+ LANG +'.lst'
nolemma_list_file = TOPICS_DIR + 'topics_'+ LANG +'.lst'

excluded_filename = TOPICS_DIR + 'topics_' + LANG + '-not_in_model.lst'

lemma_list_file_excluded = TOPICS_DIR + 'topics_lemma_excluded_' + LANG + '.lst'
nolemma_list_file_excluded = TOPICS_DIR + 'topics_excluded_' + LANG + '.lst'


In [4]:
# load the big model
model_big = KeyedVectors.load_word2vec_format(model_orig_filename, binary=True)

In [5]:
#load pickled lemma list
with open(pickled_words_lemmas, 'rb') as f:
    all_words_lemmas = pickle.load(f)
pprint(all_words_lemmas[:50])

[('και', 'και'),
 ('του', 'του'),
 ('το', 'το'),
 ('της', 'της'),
 ('να', 'να'),
 ('την', 'την'),
 ('με', 'με'),
 ('από', 'από'),
 ('για', 'για'),
 ('που', 'που'),
 ('η', 'η'),
 ('των', 'των'),
 ('τα', 'τα'),
 ('σε', 'σε'),
 ('είναι', 'είναι'),
 ('στο', 'στο'),
 ('ο', 'ο'),
 ('τον', 'τον'),
 ('στην', 'στην'),
 ('τους', 'τους'),
 ('τη', 'τη'),
 ('Η', 'η'),
 ('θα', 'θα'),
 ('τις', 'τις'),
 ('οι', 'οι'),
 ('δεν', 'δεν'),
 ('ότι', 'ότι'),
 ('Ο', 'ο'),
 ('Το', 'το'),
 ('στη', 'στη'),
 ('ή', 'ή'),
 ('περισσότερα', 'περισσότερος'),
 ('ένα', 'ένα'),
 ('Διαβάστε', 'διαβάστε'),
 ('μας', 'μας'),
 ('μια', 'μια'),
 ('στα', 'στα'),
 ('σας', 'σας'),
 ('στον', 'στον'),
 ('στις', 'στις'),
 ('έχει', 'έχω'),
 ('ήταν', 'ήταν'),
 ('αλλά', 'αλλά'),
 ('ως', 'ως'),
 ('αυτό', 'αυτό'),
 ('Οι', 'οι'),
 ('μου', 'μου'),
 ('κατά', 'κατά'),
 ('όπως', 'όπως'),
 ('αυτή', 'αυτή')]


In [6]:
# generate helpful dictionaries/lists
big_lemmas_set = set([l for (_,l) in all_words_lemmas])
print(len(big_lemmas_set))

big_words_set = set([w for (w,_) in all_words_lemmas])
print(len(big_words_set))

lemmas = {}
words_lower_orig = {}
big_lemma_word_dic = {}
big_word_lemma_dic = {}
for (w,l) in all_words_lemmas:
    big_word_lemma_dic[w] = l
    
    #dictionary of lowercase word -> all original words
    if w.lower() in words_lower_orig:
        words_lower_orig[w.lower()].append(w)
    else:
        words_lower_orig[w.lower()] = [w]
        
    if l in big_lemma_word_dic:
        big_lemma_word_dic[l].append(w)
        lemmas[l] += 1
    else:
        big_lemma_word_dic[l] = [w]
        lemmas[l] = 1
        
# load all the words from big model
words = model_big.wv.index2word
words_lower = [w.lower() for w in words]

#words_lemma = model_lemma_big.index2word       

1165112
1638268


/home/dzon/kajo/kajo_semexp_core/lib/python3.6/site-packages/ipykernel_launcher.py:29: DeprecationWarning: Call to deprecated `wv` (Attribute will be removed in 4.0.0, use self instead).


In [7]:
# sort the lemmas from most frequent
sorted_lemmas = sorted(lemmas.items(), key=operator.itemgetter(1), reverse=True)
# trying first words
sorted_lemmas[:20]

[('έχω', 30),
 ('πηγαίνω', 28),
 ('περνώ', 27),
 ('παίζω', 24),
 ('βλέπω', 24),
 ('συζητώ', 24),
 ('ζητώ', 23),
 ('βγαίνω', 23),
 ('αγαπώ', 23),
 ('πονώ', 23),
 ('πετώ', 22),
 ('ρωτώ', 22),
 ('περπατώ', 22),
 ('μπορώ', 21),
 ('αλλάζω', 21),
 ('πέφτω', 21),
 ('παρακαλώ', 21),
 ('κρατώ', 21),
 ('συναντώ', 21),
 ('προχωρώ', 21)]

In [8]:
# create vectors for the small models - average vectors for lemmas
# process only first MAX_WORDS in the big model
tmp_words = [None] * len(model_big.wv.index2word)
tmp_vecs = [None] * len(model_big.wv.index2word) 
for i,(word,lemma) in enumerate(all_words_lemmas[:MAX_WORDS]):
    lemma_words_list = big_lemma_word_dic[lemma]
    # add only lemmas made from at least 2 words
    if len(lemma_words_list)<2:
        continue
    tmp_vectors = []
    tmp_indexes = []
    error_with_word = False
    for word2 in lemma_words_list:
        try:
            tmp_vectors.append(model_big[word2])  
            tmp_indexes.append(model_big.vocab[word2].index)
        except:
            print(i, "error with ", word, " lemma ", lemma, "words", lemma_words_list)
            error_with_word = True
            continue
    if not error_with_word:
        try:
            tmp_words[min(tmp_indexes)] = lemma
            tmp_vecs[min(tmp_indexes)] = list(np.average(tmp_vectors, axis=0))
        except:
            print(i, "error with lemma ", lemma, " - words", lemma_words_list, " indexes: ", tmp_indexes)
            # note - we are processing first MAX_WORDS from the model after the filter out of the "non-words"
            # so some of the last words in that range may refer to words on bigger index than MAX_WORDS

# filter the lists (some positions remained None)
final_words = [i for i in tmp_words if i] 
final_vecs = [i for i in tmp_vecs if i != None] 

print(len(final_vecs), len(final_words))
len(final_vecs[0])  

del tmp_vecs
del tmp_words

/home/dzon/kajo/kajo_semexp_core/lib/python3.6/site-packages/ipykernel_launcher.py:3: DeprecationWarning: Call to deprecated `wv` (Attribute will be removed in 4.0.0, use self instead).
  This is separate from the ipykernel package so we can avoid doing imports until
/home/dzon/kajo/kajo_semexp_core/lib/python3.6/site-packages/ipykernel_launcher.py:4: DeprecationWarning: Call to deprecated `wv` (Attribute will be removed in 4.0.0, use self instead).
  after removing the cwd from sys.path.


184171 184171


In [9]:
# create new gensim word2vec model with the vectors:
new_vector_space = gensim.models.keyedvectors.Word2VecKeyedVectors(300)
new_vector_space.add(final_words,final_vecs)

In [10]:
# test the model
pprint(new_vector_space.most_similar('πατέρας'))
pprint(new_vector_space.most_similar_cosmul(positive=['γυναίκα', 'βασιλιάς'], negative=['άνδρας']))

[('γιος', 0.6702072024345398),
 ('πατέρα', 0.6602298021316528),
 ('παππούς', 0.6584538221359253),
 ('θείος', 0.6373026371002197),
 ('γιό', 0.6281626224517822),
 ('μπαμπάς', 0.6207959651947021),
 ('πατριός', 0.6160150766372681),
 ('πατήρ', 0.6115747690200806),
 ('γυιός', 0.5957434177398682),
 ('θετός', 0.5921958684921265)]
[('βασίλισσα', 0.9108223915100098),
 ('βασιλί', 0.8604667782783508),
 ('συμβασιλιά', 0.8314143419265747),
 ('βασιλία', 0.830093502998352),
 ('αντιβασιλιάς', 0.8286290168762207),
 ('πριγκιπα', 0.8262167572975159),
 ('βασιλισσας', 0.8253403306007385),
 ('αυτοκράτειρα', 0.8250391483306885),
 ('βασίλισσά', 0.8231985569000244),
 ('βασιλια', 0.8190919160842896)]


In [11]:
# save the model
new_vector_space.save_word2vec_format(model_filename, binary=True)

In [12]:
#model = KeyedVectors.load_word2vec_format(model_filename, binary=True)
model = new_vector_space
words_model = model.wv.index2word

/home/dzon/kajo/kajo_semexp_core/lib/python3.6/site-packages/ipykernel_launcher.py:3: DeprecationWarning: Call to deprecated `wv` (Attribute will be removed in 4.0.0, use self instead).
  This is separate from the ipykernel package so we can avoid doing imports until


In [13]:
# load topic listst
with open(nolemma_list_file) as fp:
    topics_nolemma = fp.readlines() 
print(len(topics_nolemma))
    
# load the lemma list
# with open(lemma_list_file) as fp:
#    topics = fp.readlines()
# print(len(topics))

topics = []
# generate the lemma list
for topic in tqdm(topics_nolemma):
    topic = re.sub('\W',' ',topic)
    topic = re.sub('\ +',' ',topic)
    doc = nlp(topic.strip().lower())
    lemmas = []
        
    for token in doc:
        if token.is_stop:
            continue
        lemmas.append(token.lemma_)    
    if len(lemmas) == 0:
        print('lemmas = 0 ', topics_nolemma)
    topics.append("_".join(lemmas))
    
print(len(topics))    
    
#write the lemma topic list
with open(lemma_list_file, 'wt', encoding='utf8') as f:
    for topic_lemma in topics:
        f.write(topic_lemma + "\n")    

  0%|          | 13/5305 [00:00<00:41, 126.80it/s]

5305


100%|██████████| 5305/5305 [00:26<00:00, 197.61it/s]

5305


In [14]:
print(len(topics),len(topics_nolemma))  

5305 5305


In [15]:
#try if the topic-lemma words exist in the models  

words_to_manual_add = {}

for i, (topic, topic_nolemma) in enumerate(zip(topics, topics_nolemma)):
    # process the nolemma topic so we can see which word was lemmatized to which lemma
    topic_nolemma = re.sub('\W',' ',topic_nolemma)
    topic_nolemma = re.sub('\ +',' ',topic_nolemma)
    doc = nlp(topic_nolemma.strip().lower())
    nolemmas = []
    for token in doc:
        if token.is_stop:
            continue
        else:
            nolemmas.append(token.text)  
    
    topic = topic.strip()
    topic_words = topic.split('_')
    if len(topic_words) != len(nolemmas):
        print("!!!!! error - not equal length: ", nolemmas, topic_words)
        continue
    for word, word_nolemma in zip(topic_words, nolemmas):
        #print(word)
        found = 0
        if word in words_model:
            found = 1
            #print("l1")
        elif word in big_lemmas_set:
            found = 1
            print("l2", word)
        elif word in words_lower:
            found = 1
            print("l3", word)
        # nolemma words are in PL case probably not needed and all lemmas exist in lemma list
        elif word_nolemma in words_model:
            found = 1
            print("w1", word)
        elif word_nolemma in big_lemmas_set:
            found = 1
            print("w2", word)
        elif word_nolemma in words_lower:
            found = 1
            print("w3", word)

        if found == 0:
            print(i, 'needs to be added manually: ', word, " - ", word_nolemma, " - ", topic_nolemma.strip())
            if word not in words_to_manual_add:
                words_to_manual_add[word] = topic_nolemma.strip()
                    
print(len(words_to_manual_add))          

w1
l3 τροφίμα
w3
w3
l2 γλυκέος
w3
w3
w3
w3
l3 τροφίμα
w3
w3
w3
l3 ανανεώσιμος
l3 υδατικούς
l2 τριτοβάθμιος
l2 βιώσιμης
l3 τροφίμα
l2 αλάτωση
w3
l2 αλάτωση
w3
l2 αρχιτεκτονική
w1
l2 ικος
w1
w3
l3 τροφίμα
w3
l3 νεοπαγής
l2 έγγειες
l3 τροφίμα
l2 γεωργίας
w3
w3
192 needs to be added manually:  προνομοιούχα  -  προνομοιούχα  -  μη προνομοιούχα στρώματα
w3
l2 γλυκέος
w3
w1
w3
w1
l3 λεκάνης
w3
w1
w3
w2
l2 εμπόριος
l3 τροφίμα
l3 τροφίμα
w3
w3
l2 εκτρεφόμενος
w3
l3 τροφίμα
l3 κανόνα
w1
l2 διαποτισμό
w3
w3
w1
l3 επίπλα
l2 πλημυρισμένος
w3
l3 χερσαίες
w3
w3
w3
w3
l2 παραποτάμιος
l2 γερμανία
l2 ιατρική
w3
l2 αειφόρος
w3
w3
w1
l2 γλυκέος
w3
w1
l3 μοντέλος
w3
w1
l3 τροφίμα
l3 ξυλεία
l2 μετφορά
l3 τροφίμα
w3
w3
l2 αρχιτεκτονική
w3
w3
l2 επεξεργασίας
w3
l3 θαλάσσιες
416 needs to be added manually:  ζωοφυσιολογίας  -  ζωοφυσιολογία  -  ζωοφυσιολογία
l2 έγγειος
w3
421 needs to be added manually:  θρύβου  -  θρύβου  -  επίπτωση θρύβου
w3
l2 ξηρικός
w1
w1
w3
w2
w2
w3
l2 τριτογενής
l2 πρακτική
w1
l2 επιστή

l2 εμποροβιομηχανικός
l3 οικοσυστήματος
w3
l2 θίνα
l2 απερήμωση
2063 needs to be added manually:  υπερτροφισμό  -  υπερτροφισμός  -  υπερτροφισμός
w1
2068 needs to be added manually:  ρεικότοπο  -  ρεικότοπος  -  ρεικότοπος
w1
2074 needs to be added manually:  βιοαπος  -  βιοαπο  -  βιοαπο ικο δόμηση
2077 needs to be added manually:  μαυρόχωμα  -  μαυρόχωμα  -  μαυρόχωμα
w3
2090 needs to be added manually:  ποταμοκόλπο  -  ποταμοκόλπων  -  βιολογία ποταμοκόλπων
w3
l2 επεξεργασίας
w3
l2 ασίο
w1
l2 επικίνδυνων
2113 needs to be added manually:  εκτοπισθείς  -  εκτοπισθείς  -  εκτοπισθείς εκτοπισμένο άτομο
l2 εκτοπισμένος
l3 αφρική
2122 needs to be added manually:  ποταμοκόλπο  -  ποταμοκόλπων  -  ωκεανογραφία ποταμοκόλπων
l2 αλάτωση
l3 άγριας
w1
2147 needs to be added manually:  υποστράγγιση  -  υποστράγγιση  -  υποστράγγιση
l2 μανγκρόβια
l3 αναπτυσσόμενες
2169 needs to be added manually:  χορτοδοτικό  -  χορτοδοτικό  -  χορτοδοτικό φυτό
w1
2180 needs to be added manually:  γεωργοδασοπονί

w3
l2 επικίνδυνης
w1
l2 υδρονομικός
3622 needs to be added manually:  πισσούχο  -  πισσούχος  -  πισσούχος σχιστόλιθος
w3
w1
l2 καταλύματο
l2 εξαφανισθέν
l2 οικοτοξικολογικός
w3
3652 needs to be added manually:  χλοόστρωμο  -  χλοόστρωμα  -  ξηρός χλοοτάπητας ξηρό χλοόστρωμα
w1
l2 αζώτο
l2 ενοργάνιση
l2 υαλοποίηση
l2 αζωτοδέσμευση
w1
w3
l2 αλογονωμένος
w3
l2 ρυπασμένη
l2 θορύβο
l2 ύβωμα
w3
l2 λιμνολογίο
3719 needs to be added manually:  αεριόμορφος  -  αεριόμορφος  -  αεριόμορφος ρύπος της ατμόσφαιρας
3732 needs to be added manually:  αμμοεπίπεδο  -  αμμοεπίπεδο  -  αμμοεπίπεδο
w1
3737 needs to be added manually:  ίζουσος  -  ίζουσα  -  ιον τ ίζουσα ακτινοβολία
l2 υδρογονάνθρακας
l2 απαερίων
l2 καυσαερίο
3756 needs to be added manually:  αλικυκλικός  -  αλικυκλική  -  αλικυκλική ένωση
w3
l2 αποχλωρίωση
l2 δακτυλίωση
w2
w3
l2 απηρχαιωμένη
l2 μετάλλα
w3
3788 needs to be added manually:  διάθεσση  -  διάθεσση  -  διάθεσση αποβλήτων στο έδαφος
3791 needs to be added manually:  πλημυρός  - 

w1
l3 ορνιθολογίας
4832 needs to be added manually:  χλωροφθοράνθρακα  -  χλωροφθοράνθρακας  -  χλωροφθοράνθρακας
w3
l2 άνουρα
w2
4850 needs to be added manually:  πολυτερεφθαλικό  -  πολυτερεφθαλικό  -  πολυτερεφθαλικό αιθυλένιο πεγοτεράτη
4850 needs to be added manually:  πεγοτεράτη  -  πεγοτεράτη  -  πολυτερεφθαλικό αιθυλένιο πεγοτεράτη
l2 χελώνι
w3
l2 άνυσμα
l2 κονιορτός
l2 οπτάνθρακα
l2 βιορυθμός
4878 needs to be added manually:  πολυχλωριωμένο  -  πολυχλωριωμένο  -  πολυχλωριωμένο τερφαινύλιο
4878 needs to be added manually:  τερφαινύλιο  -  τερφαινύλιο  -  πολυχλωριωμένο τερφαινύλιο
l2 βιοκλιματολογία
l2 ιχνηθέτης
l3 χρωματογραφίας
w1
4890 needs to be added manually:  κροκοδειλίδε  -  κροκοδειλίδες  -  κροκοδειλίδες
l2 διεργαστηριακός
l2 δνσο
l2 βρυόφυτα
4901 needs to be added manually:  βιοφωσφορισμός  -  βιοφωσφορισμός  -  βιοφωσφορισμός
l2 συμπλοκοποίηση
l2 αντιρρυπαντικό
l2 υψικαμίνος
4907 needs to be added manually:  ενυποθήκου  -  ενυποθήκου  -  κατάσχεση ενυποθήκου
4911 n

In [16]:
# for manual correcting of words
pprint(words_to_manual_add)

{'ίζουσες': 'σύνδρομο οφειλόμενο σε ιον τ ίζουσες ακτινοβολίες',
 'ίζουσος': 'ιον τ ίζουσα ακτινοβολία',
 'αγροσύστημας': 'αγροσύστημα',
 'αεριοχρωματογραφίας': 'αεριοχρωματογραφία',
 'αεριόμορφος': 'αεριόμορφος ρύπος της ατμόσφαιρας',
 'αεροβιολογίο': 'αεροβιολογία',
 'αλικυκλικός': 'αλικυκλική ένωση',
 'αλογονωμένη': 'αλογονωμένη ένωση',
 'αλογονωμένο': 'αλογονωμένο διφαινύλιο',
 'αμιαντίαση': 'αμιαντίαση',
 'αμμοεπίπεδο': 'αμμοεπίπεδο',
 'αμμοθίνα': 'αμμοθίνα',
 'αμμωνιοποίηση': 'αμμωνιοποίηση',
 'ανεμοθλασίας': 'ανεμοθλασία',
 'ανταγονιστικός': 'ανταγονιστική δράση τοξικών ουσιών',
 'αντιπλημυρικό': 'αντιπλημυρικό ανάχωμα',
 'αντιπλημυρικός': 'αντιπλημυρική προστασία',
 'απαερίωση': 'απαερίωση στο χώρο ταφής απορριμμάτων',
 'αποικοδομήσιμη': 'ελαφρώς αποικοδομήσιμη διασπάσιμη ουσία',
 'αποικοδομησιμότηα': 'αποικοδομησιμότητα',
 'αποτιθέμενο': 'ροές αποβλήτων αποτιθέμενων σε χώρους υγειονομικής ταφής',
 'αποϊονισμό': 'αποϊονισμός του νερού',
 'αρκτιός': 'Αρκτιός ωκεανός',
 'αρχίπτερ

In [17]:
# the lemmas not in model were manually checked if they exist in other models in some variation
word = "φυτοκομείο"
print(word)
try:
    model[word]
    print('model')
    pprint(model.most_similar(word))
except:
    pass

if word in big_lemmas_set:
    print('model_lemma_big', big_lemma_word_dic[word])

try:
    model_big[word]
    print('model big')
    pprint(model_big.most_similar(word))
except:
    pass

# if the original word with uppercase
if word in words_lower_orig:
    print('model big LOWER', words_lower_orig[word])
    pprint(model_big.most_similar(words_lower_orig[word]))
    

φυτοκομείο


In [18]:
# for cases the lemmas aren't correct or don't exist in the dic
# manually made dictionary of "lemma" : "word which exists in some model" or "word1;word2" for the average
# e.g. 'mikroekosystém': 'mikro;ekosystém', 'bahný': 'bahno'
new_words_manually_checked = {}
    
len(new_words_manually_checked)

0

In [19]:
# function which finds the word in all the available models and returns it's vector (average vector)
def get_vector(word):
    # word is in small model
    try:
        return model[word]
    except:
        pass
    
    # word is in lemmas from big model - return average if the lemma was result of more words
    if word in big_lemmas_set:
        lemma_words_list = big_lemma_word_dic[word]
        tmp_vectors = []
        for word2 in lemma_words_list:
            tmp_vectors.append(model_big[word2])  
        return np.average(tmp_vectors, axis=0)

    try:
        return model_big[word]
    except:
        pass
    
    # if the original word with uppercase
    if word in words_lower_orig:
        orig_words_list = words_lower_orig[word]
        tmp_vectors = []
        for word2 in orig_words_list:
            tmp_vectors.append(model_big[word2])  
        return np.average(tmp_vectors, axis=0)

        #return model_big[words_lower_orig[word]]
    
    return []

In [20]:
# check if the word vectors are the same
#get_vector('Antarktyki') == get_vector('antarktyki')
get_vector('διβενζοφουράνιο')

[]

In [21]:
# ading words from manually checked list
new_vectors = []
new_words = []
for i, word in enumerate(new_words_manually_checked.keys()):
    
    tmp_vectors = []
    print(i, word)
    for tmp_word in new_words_manually_checked[word].split(';'):
        vector = get_vector(tmp_word)
        if vector != []:
            tmp_vectors.append(vector)
        else:
            print("XXX - some ERROR, word doesn't have vector, cannot add: ", tmp_word)
    if word not in new_words:
        new_vectors.append(np.average(tmp_vectors, axis=0))
        new_words.append(word)
print(len(new_vectors),len(new_words))        

0 0


In [22]:
# add new words to the model
if len(new_words) > 0:
    model.add(new_words,new_vectors)

In [23]:
print(len(topics),len(topics_nolemma))  

5305 5305


In [24]:
# 2nd run - checking if there are still unavailable words in topics
excluded_topics = []
#try if the topic-lemma words exist in the model   

for i, (topic, topic_nolemma) in enumerate(zip(topics, topics_nolemma)):
    # process the nolemma topic so we can see which word was lemmatized to which lemma
    topic_nolemma_orig = topic_nolemma.strip()
    topic_nolemma = re.sub('\W',' ',topic_nolemma)
    topic_nolemma = re.sub('\ +',' ',topic_nolemma)
    doc = nlp(topic_nolemma.strip().lower())
    nolemmas = []
    for token in doc:
        if token.is_stop:
            continue
        else:
            nolemmas.append(token.text)  
    
    topic_words = topic.split('_')
    
    if len(topic_words) != len(nolemmas):
        print("!!!!! error - not equal length: ", nolemmas, topic_words)
        continue
        
    found = 1
    for word, word_nolemma in zip(topic_words, nolemmas):
    #for word in topic_words:
        #print(word)
       
        vector = get_vector(word)
        if vector == []:
            print('nonexistend word: ', word, " - ", topic_nolemma)
            vector2 = get_vector(word_nolemma)
            if vector2 == []:
                found = 0
                print('nonexistend word: ', word_nolemma, " - ", topic_nolemma)
            else:
                print("Exist nolemma")

    if found == 0:
        print('!!! topic needs to be excluded: ', topic_nolemma_orig)
        if topic_nolemma.strip() not in excluded_topics:
            excluded_topics.append(topic_nolemma_orig)
                    
print(len(excluded_topics)) 

nonexistend word:  βιομηχανίος  -  βιομηχανία ειδών διατροφής 
Exist nolemma


/home/dzon/kajo/kajo_semexp_core/lib/python3.6/site-packages/ipykernel_launcher.py:30: DeprecationWarning: elementwise comparison failed; this will raise an error in the future.
/home/dzon/kajo/kajo_semexp_core/lib/python3.6/site-packages/ipykernel_launcher.py:33: DeprecationWarning: elementwise comparison failed; this will raise an error in the future.


nonexistend word:  υδάτο  -  διαχείριση των υδάτων 
Exist nolemma
nonexistend word:  ύδατο  -  οικοσύστημα σε γλυκά ύδατα γλυκέων υδάτων 
Exist nolemma
nonexistend word:  υδάτο  -  οικοσύστημα σε γλυκά ύδατα γλυκέων υδάτων 
Exist nolemma
nonexistend word:  πλωτέ  -  εσωτερικές πλωτές μεταφορές 
Exist nolemma
nonexistend word:  υδάτο  -  διαχείριση της ποιότητας των υδάτων 
Exist nolemma
nonexistend word:  υδάτο  -  διαχείριση των επιφανειακών υδάτων 
Exist nolemma
nonexistend word:  υδάτο  -  δημοτική διαχείριση υδάτων 
Exist nolemma
nonexistend word:  ύδατο  -  επιφανειακά ύδατα 
Exist nolemma
nonexistend word:  υδάτο  -  διαχείριση της ποσότητας των υδάτων 
Exist nolemma
nonexistend word:  υδάτο  -  αλάτωση των υδάτων 
Exist nolemma
nonexistend word:  υδάτο  -  παρακολούθηση των υδάτων 
Exist nolemma
nonexistend word:  οικολογίος  -  οικολογία υγροτόπων 
Exist nolemma
nonexistend word:  βιομηχανίος  -  βιομηχανία ποτών 
Exist nolemma
nonexistend word:  ύδατο  -  γλυκά ύδατα 
Exist no

nonexistend word:  μεταφορός  -  δίκαιο των μεταφορών 
Exist nolemma
nonexistend word:  υδάτο  -  αφαίρεση απόληψη υδάτων 
Exist nolemma
nonexistend word:  επιχειρήσεο  -  οικονομική των επιχειρήσεων 
Exist nolemma
nonexistend word:  θηραμάτα  -  φυσικό καταφύγιο εκτροφείο θηραμάτων 
Exist nolemma
nonexistend word:  αποϊονισμό  -  αποϊονισμός του νερού 
nonexistend word:  αποϊονισμός  -  αποϊονισμός του νερού 
!!! topic needs to be excluded:  αποϊονισμός του νερού
nonexistend word:  ύδατο  -  εκπομπές στα ύδατα 
Exist nolemma
nonexistend word:  ύδατο  -  θερμικά ύδατα 
Exist nolemma
nonexistend word:  χρήσεο  -  νομοθεσία περί χωροταξίας πολεοδομίας και χρήσεων γης 
Exist nolemma
nonexistend word:  πλεονάζουσος  -  απωλεσθείσα πλεονάζουσα θερμότητα 
Exist nolemma
nonexistend word:  ύδατο  -  χωρικά ύδατα 
Exist nolemma
nonexistend word:  ύδατο  -  χρησιμοποιημένα ύδατα 
Exist nolemma
nonexistend word:  υδάτο  -  έκθεση των υδάτων σε κίνδυνο 
Exist nolemma
nonexistend word:  υδάτο  -  π

nonexistend word:  λυμάτα  -  επεξεργασία λυμάτων 
Exist nolemma
nonexistend word:  υδροψυχαγωγία  -  εγκαταστάσεις υδροψυχαγωγίας 
nonexistend word:  υδροψυχαγωγίας  -  εγκαταστάσεις υδροψυχαγωγίας 
!!! topic needs to be excluded:  εγκαταστάσεις υδροψυχαγωγίας
nonexistend word:  δοικά  -  ντόπια δοικά υλικά 
nonexistend word:  δοικά  -  ντόπια δοικά υλικά 
!!! topic needs to be excluded:  ντόπια δοικά υλικά
nonexistend word:  ύδατο  -  ύδατα για γεωργική χρήση 
Exist nolemma
nonexistend word:  λυμάτα  -  φορτίο φόρτος λυμάτων 
Exist nolemma
nonexistend word:  λυμάτα  -  διάθεση αποχέτευση των λυμάτων 
Exist nolemma
nonexistend word:  μεταφορός  -  επιπτώσεις των μεταφορών στο περιβάλλον 
Exist nolemma
nonexistend word:  βιομηχανίος  -  βιομηχανία παραγωγής ηλεκτρικών 
Exist nolemma
nonexistend word:  πρωτείνε  -  τροφή με υψηλή περιεκτικότητα σε πρωτείνες 
Exist nolemma
nonexistend word:  πετερελαϊκός  -  διατήρηση πετερελαϊκών πόρων 
nonexistend word:  πετερελαϊκών  -  διατήρηση πετε

...

nonexistend word:  απόβληα  -  απόβλητα απορρίμματα νοσοκομείου 
Exist nolemma
nonexistend word:  απορρίμματας  -  απόβλητα απορρίμματα νοσοκομείου 
Exist nolemma
nonexistend word:  αποικοδομησιμότηα  -  αποικοδομησιμότητα 
nonexistend word:  αποικοδομησιμότητα  -  αποικοδομησιμότητα 
!!! topic needs to be excluded:  αποικοδομησιμότητα
nonexistend word:  ιλύο  -  χώνευση της ιλύος 
Exist nolemma
nonexistend word:  οξιδωτικό  -  οξιδωτικό υλικό 
nonexistend word:  οξιδωτικό  -  οξιδωτικό υλικό 
!!! topic needs to be excluded:  οξιδωτικό υλικό
nonexistend word:  όριος  -  προδιαγεγραμμένα όρια εκπομπών 
Exist nolemma
nonexistend word:  βιοδιαθεσιμότητο  -  βιοδιαθεσιμότητα 
Exist nolemma
nonexistend word:  ύδατο  -  χώνευση ακάθαρτα ύδατα 
Exist nolemma
nonexistend word:  πεδίος  -  πεδίο ροής 
Exist nolemma
nonexistend word:  πράξεο  -  αιτιολόγηση αιτιολογικό των διοικητικών πράξεων 
Exist nolemma
nonexistend word:  κασπίος  -  Κασπία Θάλασσα 
Exist nolemma
nonexistend word:  λυμάτα  -

nonexistend word:  οξιδοαναγωγή  -  οξιδοαναγωγή 
nonexistend word:  οξιδοαναγωγή  -  οξιδοαναγωγή 
!!! topic needs to be excluded:  οξιδοαναγωγή
nonexistend word:  ιχθυαπόθεμα  -  ιχθυαπόθεμα 
nonexistend word:  ιχθυαπόθεμα  -  ιχθυαπόθεμα 
!!! topic needs to be excluded:  ιχθυαπόθεμα
nonexistend word:  κυκλοφορίο  -  εναέρια κυκλοφορία πολιτικής αεροπορίας 
Exist nolemma
nonexistend word:  απορρίμματας  -  καταναλωτικά απορρίμματα 
Exist nolemma
nonexistend word:  ερυθρόχρωμο  -  έξαρση ερυθρόχρωμου πλαγκτού 
nonexistend word:  ερυθρόχρωμου  -  έξαρση ερυθρόχρωμου πλαγκτού 
!!! topic needs to be excluded:  έξαρση ερυθρόχρωμου πλαγκτού
nonexistend word:  ταχείος  -  ταχεία κυκλοφορία 
Exist nolemma
nonexistend word:  κυκλοφορίο  -  ταχεία κυκλοφορία 
Exist nolemma
nonexistend word:  οξιδωτικό  -  φωτοχημικό οξιδωτικό μέσο 
nonexistend word:  οξιδωτικό  -  φωτοχημικό οξιδωτικό μέσο 
!!! topic needs to be excluded:  φωτοχημικό οξιδωτικό (μέσο)
nonexistend word:  βόεϊο  -  βόεϊος 
nonexi

nonexistend word:  ίγμος  -  μ ε ίγμα αερίων 
Exist nolemma
nonexistend word:  απορριμμάτος  -  χώρος υγειονομικής ταφής απορριμμάτων ΧΥΤΑ 
Exist nolemma
nonexistend word:  νοσήμαα  -  νοσήματα παθήσεις 
Exist nolemma
nonexistend word:  οφέλου  -  ανάλυση κινδύνου οφέλους 
Exist nolemma
nonexistend word:  σπανίζον  -  σπάνιο σπανίζον είδος 
nonexistend word:  σπανίζον  -  σπάνιο σπανίζον είδος 
!!! topic needs to be excluded:  σπάνιο (σπανίζον) είδος
nonexistend word:  υδατοπαροχή  -  μέτρηση υδατοπαροχής 
nonexistend word:  υδατοπαροχής  -  μέτρηση υδατοπαροχής 
!!! topic needs to be excluded:  μέτρηση υδατοπαροχής
nonexistend word:  απόβληα  -  απόβλητα εργαστηρίου 
Exist nolemma
nonexistend word:  αναψυχός  -  ορεινό κέντρο αναψυχής καταφύγιο 
Exist nolemma
nonexistend word:  απόβληα  -  υγρά απόβλητα 
Exist nolemma
nonexistend word:  άλατο  -  περιεκτικότητα άλατος σε άλατα 
Exist nolemma
nonexistend word:  αεριοχρωματογραφίας  -  αεριοχρωματογραφία 
nonexistend word:  αεριοχρωματο

nonexistend word:  οδοντόγναθος  -  οδοντόγναθα λιβελούλες 
Exist nolemma
nonexistend word:  εναποτεθημένα  -  Εναποτεθημένα 
nonexistend word:  εναποτεθημένα  -  Εναποτεθημένα 
!!! topic needs to be excluded:  Εναποτεθημένα
nonexistend word:  ρυπαίνο  -  αρχή ο ρυπαίνων πληρώνει 
Exist nolemma
nonexistend word:  απόβληα  -  δύσκολα διαθέσιμα απόβλητα 
Exist nolemma
nonexistend word:  μηχάνημος  -  μηχάνημα καθαρισμού αέρα με ψεκασμό νερού 
Exist nolemma
nonexistend word:  κρουαζέρας  -  κρουαζέρα 
nonexistend word:  κρουαζέρα  -  κρουαζέρα 
!!! topic needs to be excluded:  κρουαζέρα
nonexistend word:  υδατομετρία  -  υδατομετρία 
nonexistend word:  υδατομετρία  -  υδατομετρία 
!!! topic needs to be excluded:  υδατομετρία
nonexistend word:  αρχίπτερα  -  αρχίπτερα 
nonexistend word:  αρχίπτερα  -  αρχίπτερα 
!!! topic needs to be excluded:  αρχίπτερα
nonexistend word:  αλογονωμένο  -  αλογονωμένο διφαινύλιο 
nonexistend word:  αλογονωμένο  -  αλογονωμένο διφαινύλιο 
!!! topic needs to 

nonexistend word:  πολυχλωριωμένο  -  πολυχλωριωμένο διφαινύλιο 
nonexistend word:  πολυχλωριωμένο  -  πολυχλωριωμένο διφαινύλιο 
!!! topic needs to be excluded:  πολυχλωριωμένο διφαινύλιο
nonexistend word:  παραγραφός  -  παραγραφή χρέους 
Exist nolemma
nonexistend word:  φυκοκτόνο  -  φυκοκτόνο 
nonexistend word:  φυκοκτόνο  -  φυκοκτόνο 
!!! topic needs to be excluded:  φυκοκτόνο
nonexistend word:  γεωδεδομένος  -  γεωδεδομένα αναφοράς 
Exist nolemma
nonexistend word:  διχλωροδιφαινυλτριχλωροαιθάνιο  -  DDT διχλωροδιφαινυλτριχλωροαιθάνιο 
nonexistend word:  διχλωροδιφαινυλτριχλωροαιθάνιο  -  DDT διχλωροδιφαινυλτριχλωροαιθάνιο 
!!! topic needs to be excluded:  DDT (διχλωροδιφαινυλτριχλωροαιθάνιο)
nonexistend word:  εγκυκλοπαίδειο  -  εγκυκλοπαίδεια 
Exist nolemma
nonexistend word:  κορέοι  -  κορέοι 
nonexistend word:  κορέοι  -  κορέοι 
!!! topic needs to be excluded:  κορέοι
nonexistend word:  χρωματομετρίο  -  χρωματομετρία 
Exist nolemma
nonexistend word:  ισομερά  -  ισομερές 
E

In [25]:
# save topics containing words which are not present neither model - to be excluded from the topic list
print('excluded topics: ', len(excluded_topics))
pprint(excluded_topics)
with open(excluded_filename, 'wt', encoding='utf8') as f:
    for topic in excluded_topics:
        f.write(topic + "\n")

excluded topics:  232
['μη προνομοιούχα στρώματα',
 'ζωοφυσιολογία',
 'επίπτωση θρύβου',
 'ζωοοικολογία',
 'μικροκλιματικό φαινόενο',
 'εδαφοβιολογία',
 'δασοκαταφύγιο',
 'μονοξίδιο του άνθρακα',
 'υδρόβιος μικρο-οραγανισμος',
 'ζωοβιολογία',
 'αποϊονισμός του νερού',
 'ζωεμπορία',
 'ωομοθετική διδικασία',
 'γουνοφόρο ζώο',
 'υδροφόρος ορίχοντας',
 'εδαφοκατατομή',
 'προστασία της άγριας χλωροπανίδας',
 'διατήρηση της άγριας χλωροπανίδας',
 'διοξίδιο του άνθρακα',
 'υδροϋάκυνθος',
 'νερόψυλλοι',
 'διαστασιοδότηση',
 'περιβαλλοντική εξειγίανση',
 'διαδικασία θερμοεπιλογής',
 'φωλεοποιό πτηνό',
 'αντιπλημυρική προστασία',
 'λειβαδικό οικοσύστημα',
 'ομβρόφιλο δάσος',
 'βιμηχανικές αναθυμιάσεις',
 'οικοσύστημα ποταμοκόλπων',
 'θρεπτικήαξία τροφίμων',
 'λεκάνη (πλημυρικής) απορροής (ομβρίων υδάτων)',
 'εγκαταστάσεις υδροψυχαγωγίας',
 'ντόπια δοικά υλικά',
 'διατήρηση πετερελαϊκών πόρων',
 'μονάδα ηλεκρτοπαραγωγής',
 'κανονισμοί ελέγχγου για την ρύπανση',
 'βιομηχανία ελαίων και γράσων (ελα

In [26]:
# create new lists which don't containt topics with non-existent words

# load list with excluded topics
with open(excluded_filename, 'rt', encoding='utf8') as fp:
    tmp_topics = fp.readlines()
excluded_set = set()
for topic in tmp_topics:
    excluded_set.add(topic.strip())

with open(nolemma_list_file, 'rt', encoding='utf8') as fp:
        topics_file = fp.readlines()

topics_final = []
topics_lemma = []

excluded = 0
for topic in topics_file:
    topic_orig = topic.strip()
    if topic_orig in excluded_set:
        print("=== EXCLUDE ", topic_orig)
        excluded += 1
        continue
    topic = re.sub('\W',' ',topic)
    topic = re.sub('\ +',' ',topic)
    doc = nlp(topic.strip().lower())
    lemmas = []

    for token in doc:
        if token.is_stop:
            continue
        lemmas.append(token.lemma_)    
    topics_lemma.append("_".join(lemmas))
    topics_final.append(topic_orig)

    print(topic_orig, ' --- ', "_".join(lemmas))

print('Excluded: ', excluded)
print('Final topics: ', len(topics_lemma), len(topics_final))
    
with open(lemma_list_file_excluded, 'wt', encoding='utf8') as f:
    for topic_lemma in topics_lemma:
        f.write(topic_lemma + "\n")
with open(nolemma_list_file_excluded, 'wt', encoding='utf8') as f:
    for topic_final in topics_final:
        f.write(topic_final + "\n")  

τοπική ανάπτυξη  ---  τοπικός_ανάπτυξη
αγροτική ανάπτυξη  ---  αγροτικός_ανάπτυξη
διαχείριση των υδατικών πόρων  ---  διαχείριση_υδατικός_πόρο
επίπεδο εκπαίδευσης  ---  επίπεδο_εκπαίδευση
γενική εκπαίδευση  ---  γενικός_εκπαίδευση
όχθη  ---  όχθη
κοινοτικό δίκαιο  ---  κοινοτικό_δίκαιο
πολιτιστική κληρονομιά  ---  πολιτιστικός_κληρονομιά
γεωργική έκταση  ---  γεωργικός_έκταση
αγροτικό τοπίο  ---  αγροτικό_τοπίο
γεωργική παραγωγή  ---  γεωργικός_παραγωγή
οικονομική ανάπτυξη  ---  οικονομικός_ανάπτυξη
τροφική αλυσίδα  ---  τροφικός_αλυσίδα
βιομηχανία ειδών διατροφής  ---  βιομηχανίος_ειδός_διατροφή
ποιότητα των τροφίμων  ---  ποιότητας_τροφίμα
επίδραση του φαινομένου του θερμοκηπίου  ---  επίδραση_φαινομένο_θερμοκηπίο
φαινόμενο του θερμοκηπίου  ---  φαινόμενο_θερμοκηπίο
βιομηχανική ανάπτυξη  ---  βιομηχανικός_ανάπτυξη
αγορά εργασίας  ---  αγορά_εργασία
χερσαία πρόσβαση  ---  χερσαίος_πρόσβαση
αναδασμός  ---  αναδασμός
χωροταξία  ---  χωροταξία
αρχιτεκτονική τοπίου  ---  αρχιτεκτονικός_το

σύστημα ασφαλείας  ---  σύστημα_ασφαλεία
υποδομή  ---  υποδομή
απολύμανση του εδάφους  ---  απολύμανση_εδάφου
βοσκότοπος  ---  βοσκότοπο
οικονομική μεγέθυνση  ---  οικονομικός_μεγέθυνση
υποβάθμιση των γλυκέων υδάτων  ---  υποβάθμιση_γλυκέος_υδάτο
τροφή  ---  τροφή
οξίνιση του εδάφους  ---  οξίνιση_εδάφου
βιολογική κληρονομιά  ---  βιολογικός_κληρονομιά
κοινοτική πράξη  ---  κοινοτικός_πράξη
αγροτικό οίκημα  ---  αγροτικό_οίκημα
βιομηχανικό κτήριο  ---  βιομηχανικό_κτήριο
κλίμα  ---  κλίμα
βιομηχανία καλλυντικών  ---  βιομηχανίος_καλλυντικός
κτηνοτροφία  ---  κτηνοτροφία
χρήση πόρων  ---  χρήση_πόρο
αξιοποίηση των υδάτων  ---  αξιοποίηση_υδάτο
χορτο(ποο-)λιβαδική έκταση  ---  χορτο_ποο_λιβαδικός_έκταση
χαλυβουργία  ---  χαλυβουργία
βιομηχανία ηλεκτρικής ενέργειας  ---  βιομηχανίος_ηλεκτρικός_ενέργεια
διαχείριση λεκάνης απορροής  ---  διαχείριση_λεκάνης_απορροή
υποβάθμιση του οικοσυστήματος  ---  υποβάθμιση_οικοσυστήματο
βιομηχανία ιματισμού  ---  βιομηχανίος_ιματισμός
κεραμική βιομηχανί

χημική βιομηχανία  ---  χημικός_βιομηχανία
Συνθήκη ΕΚ  ---  συνθήκη_εκ
οικογένεια  ---  οικογένεια
φυσική κληρονομιά  ---  φυσικός_κληρονομιά
μεταλλουργική βιομηχανία  ---  μεταλλουργικός_βιομηχανία
αβιοτικό περιβάλλον  ---  αβιοτικό_περιβάλλον
τσιμεντοβιομηχανία  ---  τσιμεντοβιομηχανία
κόστος του νερού  ---  κόστος_νερός
διεθνές δίκαιο  ---  διεθνός_δίκαιο
πρόσβαση στην πληροφόρηση  ---  πρόσβαση_πληροφόρηση
κατανάλωση ύδατος  ---  κατανάλωση_ύδατος
ύδατα για κατανάλωση  ---  ύδατο_κατανάλωση
κτήριο  ---  κτήριο
ανάλυση νερού (υδάτων)  ---  ανάλυση_νερός_υδάτο
εδαφολογική ανάλυση  ---  εδαφολογικός_ανάλυση
επίδραση (επιπτώσεις) της ρύπανσης  ---  επίδραση_επιπτώσει_ρύπανση
υποβάθμιση του περιβάλλοντος  ---  υποβάθμιση_περιβάλλον
φυσικές διαδικασίες  ---  φυσικός_διαδικασία
προστασία των ζώων  ---  προστασία_ζώο
προστασία των ζώων  ---  προστασία_ζώο
δασική προστασία  ---  δασικός_προστασία
πανίδα  ---  πανίδα
εγγύηση (διασφάλιση) ποιότητας  ---  εγγύηση_διασφάλιση_ποιότητας
χλωρή λίπ

παράκτια ρύπανση  ---  παράκτιος_ρύπανση
ρύπανση των γλυκέων υδάτων  ---  ρύπανση_γλυκέος_υδάτο
πτηνοτροφία  ---  πτηνοτροφία
ικανότητα του εδάφους  ---  ικανότητας_εδάφου
αγορά (του) περιβάλλοντος  ---  αγορά_περιβάλλον
αντλία νερού  ---  αντλία_νερός
αγορά ενέργειας  ---  αγορά_ενέργεια
συντήρηση  ---  συντήρηση
στάθμη νερού (υδάτων)  ---  στάθμη_νερός_υδάτο
αγροτικό οίκημα  ---  αγροτικό_οίκημα
επιχείρηση  ---  επιχείρηση
δημόσιο έργο  ---  δημόσιος_έργο
περιβαλλοντική ασφάλεια  ---  περιβαλλοντικός_ασφάλεια
χρηματαγορά  ---  χρηματαγορά
οικονομική δραστηριότητα  ---  οικονομικός_δραστηριότητα
βιομηχανική δραστηριότητα  ---  βιομηχανικός_δραστηριότητα
δημογραφική τάση (άνθρωποι)  ---  δημογραφικός_τάση_άνθρωποι
στεγαστικές ανάγκες  ---  στεγαστικός_ανάγκα
πολιτική για την παραγωγή  ---  πολιτική_παραγωγή
βιογεωγραφικές περιοχές  ---  βιογεωγραφικός_περιοχή
σύστημα επικοινωνίας (επικοινωνιών)  ---  σύστημα_επικοινωνία_επικοινωνία
οικοδομήσιμη γη  ---  οικοδομήσιμη_γη
χρηματοπιστωτική

περιβαλλοντικός κώδικας  ---  περιβαλλοντικός_κώδικα
επιχειρηματική πολιτική  ---  επιχειρηματικός_πολιτική
παρακολούθηση των θαλασσών  ---  παρακολούθηση_θαλασσή
διά βίου (συνεχιζόμενη) εκπαίδευση  ---  διά_βίο_συνεχιζόμενη_εκπαίδευση
αστική κοινότητα  ---  αστικός_κοινότητα
απόφαση της κοινότητας  ---  απόφαση_κοινότητα
πολιτική συντήρησης  ---  πολιτική_συντήρηση
βιομηχανικά απόβλητα  ---  βιομηχανικά_απόβληα
βιομηχανική καλλιέργεια  ---  βιομηχανικός_καλλιέργεια
ρέοντα ύδατα  ---  ρέοντος_ύδατο
απόβλητα των καλλιεργειών  ---  απόβληα_καλλιεργειής
δασική οικολογία  ---  δασικός_οικολογία
δίκαιο του ανταγωνισμού  ---  δίκαιο_ανταγωνισμός
ζωικοί πόροι  ---  ζωικός_πόροι
κτηματολόγιο  ---  κτηματολόγιο
βιομηχανική ιατρική  ---  βιομηχανικός_ιατρική
σκληρότητα του ύδατος  ---  σκληρότητα_ύδατος
φυσική γεωγραφία  ---  φυσικός_γεωγραφία
θαλάσσια αλιεία  ---  θαλάσσιος_αλιεία
υδραυλική (υδροηλεκτρική) ενέργεια  ---  υδραυλικός_υδροηλεκτρικός_ενέργεια
οικοδομική άδεια  ---  οικοδομικός_άδει

...

φαρμακολογία  ---  φαρμακολογία
απορρίμματα κήπου  ---  απορρίμματας_κήπου
παλαιά επικίνδυνη τοποθεσία (περιοχή)  ---  παλαί_επικίνδυνη_τοποθεσία_περιοχή
ναυάγιο  ---  ναυάγιο
χορήγηση αδείας  ---  χορήγηση_αδεία
ανάλυση κινδύνου  ---  ανάλυση_κινδύνο
καταχώριση (αποτύπωση) εικόνων  ---  καταχώριση_αποτύπωση_εικόνα
μαλλί  ---  μαλλί
υπερδιήθηση  ---  υπερδιήθηση
λιθόσφαιρα  ---  λιθόσφαιρος
καταστατικό κείμενο  ---  καταστατικό_κείμενο
θερμοηλεκτρικός σταθμός (παραγωγής ενέργειας)  ---  θερμοηλεκτρικός_σταθμός_παραγωγή_ενέργεια
φορτίο (φόρτος) αποβλήτων  ---  φορτίο_φόρτος_αποβλήτα
νόμος για τη διάθεση των αποβλήτων  ---  νόμος_διάθεση_αποβλήτα
ημιμέταλλο  ---  ημιμέταλλο
εξόρυξη  ---  εξόρυξη
διατήρηση της ειρήνης  ---  διατήρηση_ειρήνη
ιλύς υπολειμματικών αποβλήτων  ---  ιλύς_υπολειμματικός_αποβλήτα
πυρηνική επικινδυνότητα  ---  πυρηνικός_επικινδυνότηα
ζύμωση  ---  ζύμωση
μπαταρία  ---  μπαταρία
καυσαέριο  ---  καυσαέριο
=== EXCLUDE  νιτροένωση
αμαξοστοιχία  ---  αμαξοστοιχίας
ανοικτ

ευρετηρίαση εγγράφων (υλικού τεκμηρίωσης)  ---  ευρετηρίαση_εγγράφο_υλικός_τεκμηρίωση
διάρκεια ηλιοφάνειας  ---  διάρκειο_ηλιοφάνεια
στατιστικά στοιχεία  ---  στατιστικά_στοιχείο
πυρηνική έκρηξη (ατύχημα)  ---  πυρηνικός_έκρηξη_ατύχημα
ευθύγραμμη (επίπεδη) πηγή  ---  ευθύγραμμη_επίπεδη_πηγή
=== EXCLUDE  ραβδόγλυφα
αποτοξίνωση  ---  αποτοξίνωση
οπληφόρα  ---  οπληφόρα
δεξαμενόπλοιο (πετρελαιοφόρο) διπλού καταστρώματος  ---  δεξαμενόπλοιος_πετρελαιοφόρο_διπλός_καταστρώμα
στοιχεία της ομάδας II (αλκαλικές γαίες)  ---  στοιχείο_ομάδα_ii_αλκαλικός_γαία
γραμμική πηγή ήχου  ---  γραμμικός_πηγή_ήχο
απόρριψη πυρηνικού σταθμού  ---  απόρριψη_πυρηνικός_σταθμός
χώρος απόρριψης ραδιενεργών αποβλήτων  ---  χώρος_απόρριψη_ραδιενεργή_αποβλήτα
διαχωριστής  ---  διαχωριστής
(εμπορικό) κατάστημα  ---  εμπορικό_κατάστημα
=== EXCLUDE  αλογονωμένη φαινόλη
φαράγγι  ---  φαράγγι
φορολογία  ---  φορολογία
(χρηματική) αποζημίωση  ---  χρηματικός_αποζημίωση
υποχρέωση επισήμανσης  ---  υποχρέωση_επισήμανση
στόμιο

επικινδυνότητα των ρύπων  ---  επικινδυνότηα_ρύπο
σύστημα σταθερών τελών  ---  σύστημα_σταθερός_τελή
ημερήσια επιτρεπόμενη δόση  ---  ημερήσιος_επιτρεπόμενη_δόση
κοινοποίηση  ---  κοινοποίηση
μέσο(α) επικοινωνίας  ---  μέσο_α_επικοινωνία
χρωστική ύλη  ---  χρωστικός_ύλη
δύσκολα διαθέσιμα απόβλητα  ---  δύσκολο_διαθέσιμος_απόβληα
μηχάνημα καθαρισμού αέρα με ψεκασμό νερού  ---  μηχάνημος_καθαρισμός_αέρας_ψεκασμό_νερός
απόχυση  ---  απόχυση
=== EXCLUDE  κρουαζέρα
βιοκτόνο  ---  βιοκτόνο
καθεστώς που διέπει τις απολύσεις  ---  καθεστώς_διέπω_απολύσει
αδιάλυτη ουσία  ---  αδιάλυτη_ουσία
ακτινοβολία  ---  ακτινοβολία
υπουργείο  ---  υπουργείο
=== EXCLUDE  υδατομετρία
Ωκεανία  ---  ωκεανίας
συντελεστής βιοσυγκέντρωσης  ---  συντελεστής_βιοσυγκέντρωση
=== EXCLUDE  αρχίπτερα
φορέας δεδομένων  ---  φορέας_δεδομένο
διαβαθμισμένη τοποθεσία (περιοχή)  ---  διαβαθμισμένη_τοποθεσία_περιοχή
ποινικές ρήτρες  ---  ποινικός_ρήτρα
διαφορά  ---  διαφορά
πηγή διάχυσης  ---  πηγή_διάχυση
τέφρα  ---  τέφρα
χρ

απαγόρευση  ---  απαγόρευση
φράκτης (θάμνων)  ---  φράκτης_θάμνο
κατηγορία απειλούμενου με εξαφάνιση είδους  ---  κατηγορίο_απειλούμενος_εξαφάνιση_είδου
=== EXCLUDE  κροκοδειλίδες
αντίσωμα  ---  αντίσωμα
διεργαστηριακή σύγκριση  ---  διεργαστηριακός_σύγκριση
(εν)δείκτης  ---  δείκτης
βάριο  ---  βάριο
καταλυτικός μετατροπέας  ---  καταλυτικός_μετατροπέας
φωτεινότητα  ---  φωτεινότητο
επώαση  ---  επώαση
κώδικας ΔΝΣΟ (Διακυβερνητικού Ναυτιλιακού  ---  κώδικας_δνσο_διακυβερνητικός_ναυτιλιακός
διερεύνηση τερατογένεσης  ---  διερεύνηση_τερατογένεση
βρυόφυτα  ---  βρυόφυτα
=== EXCLUDE  βιοφωσφορισμός
δόση  ---  δόση
μέσο συμπλοκοποίησης  ---  μέσος_συμπλοκοποίηση
αντιρρυπαντικό μέσο  ---  αντιρρυπαντικό_μέσο
δηλητηρίαση  ---  δηλητηρίαση
φρέαρ υψικαμίνου  ---  φρέαρ_υψικαμίνος
=== EXCLUDE  κατάσχεση ενυποθήκου
συμπίεση  ---  συμπίεση
χώρος (σταθμός) ελιγμών  ---  χώρος_σταθμός_ελιγμός
θεματική ομάδα (φόρουμ) συζήτησης [στο Διαδίκτυο]  ---  θεματικός_ομάδα_φόρουμ_συζήτηση_διαδίκτυο
=== EXCLU

βιοδείκτης  ---  βιοδείκτης
=== EXCLUDE  πυραλένιο
γονοτοξικότητα  ---  γονοτοξικότηα
=== EXCLUDE  φωτοαποικοδόμηση
κοκκομετρία  ---  κοκκομετρία
πρωτοβάθμια καθίζηση  ---  πρωτοβάθμιος_καθίζηση
=== EXCLUDE  βιοδιήθηση
=== EXCLUDE  μεθανιοποίηση
οικολογική καταστροφή  ---  οικολογικός_καταστροφή
=== EXCLUDE  χηλικεραιωτά
χειρόπτερα  ---  χειρόπτερα
=== EXCLUDE  χρυσόφυτα
κατασκευή δικτύου  ---  κατασκευή_δικτύο
προσαρμογή στην κλιματική αλλαγή  ---  προσαρμογή_κλιματικός_αλλαγή
υπέργεια βιομάζα  ---  υπέργειος_βιομάζα
παραγωγή βιοενέργειας  ---  παραγωγή_βιοενέργεια
αγροτουρισμού  ---  αγροτουρισμός
αγρονομικό πρόσθετο λιπάσματος  ---  αγρονομικό_πρόσθετος_λιπάσματο
εγχειρίδιο για την απογραφή εκπομπών ατμοσφαιρικών ρύπων  ---  εγχειρίδιο_απογραφός_εκπομπή_ατμοσφαιρικός_ρύπο
οδηγίες για την ποιότητα του αέρα  ---  οδηγία_ποιότητας_αέρας
διαχείριση ζωικών αποβλήτων  ---  διαχείριση_ζωικός_αποβλήτα
τεχνητή γη  ---  τεχνητός_γη
Θάλασσα του Μπάρεντς  ---  θάλασσα_μπάρεντ
οδηγία περί της πο

In [28]:
# adding all the words and topics to model

# load the lemma list
with open(lemma_list_file_excluded) as fp:
    topics = fp.readlines()
# load the nolemma list
with open(nolemma_list_file_excluded) as fp:
    topics_nolemma = fp.readlines()    
    

#try if the topic-lemma words exist in the model     
new_vectors = []
new_words = []
for i, (topic, topic_nolemma) in enumerate(zip(topics, topics_nolemma)):
#for i,topic in enumerate(topics):
    topic_nolemma = re.sub('\W',' ',topic_nolemma)
    topic_nolemma = re.sub('\ +',' ',topic_nolemma)
    doc = nlp(topic_nolemma.strip().lower())
    nolemmas = []
    for token in doc:
        if token.is_stop:
            continue
        else:
            nolemmas.append(token.text) 
            
    topic = topic.strip()
    topic_words = topic.split('_')
    
    if len(topic_words) != len(nolemmas):
        print("!!!!! error - not equal length: ", nolemmas, topic_words)
        continue
    #if len(topic_words)<2:
    #    continue
    
    
    tmp_vectors = []
    
    for word, word_nolemma in zip(topic_words, nolemmas):
    #for word in topic_words:
        vector = get_vector(word)
        
        try:
            tmp_vectors.append(model[word])
        except: 
            print('\nNOT in vocabulary: ', word, topic)
            vector = get_vector(word)
            if vector != []:
                tmp_vectors.append(vector)
                if word not in new_words:
                    print('append ', word)
                    new_vectors.append(vector)
                    new_words.append(word)   
            else:
                vector = get_vector(word_nolemma)
                if vector != []:
                    tmp_vectors.append(vector)
                    if word not in new_words:
                        print('append ', word)
                        new_vectors.append(vector)
                        new_words.append(word)  
                else:
                    raise Warning(f"XXX {word} {topic} {topic_nolemma}")
                    print("XXX", word, topic, topic_nolemma) 
    #if word not in new_words:
    #    new_vectors.append(list(np.average(tmp_vectors, axis=0)))
    #    new_words.append(word)        
    if len(tmp_vectors) > 1:
        if topic not in new_words:
   
            print('append ', topic)
            new_vectors.append(list(np.average(tmp_vectors, axis=0)))
            new_words.append(topic)
        else:
            print('doubled TOPIC: ', topic)    
    else:
        print('--- only one word, not a new topic>', topic)

append  τοπικός_ανάπτυξη
append  αγροτικός_ανάπτυξη
append  διαχείριση_υδατικός_πόρο
append  επίπεδο_εκπαίδευση
append  γενικός_εκπαίδευση
--- only one word, not a new topic> όχθη
append  κοινοτικό_δίκαιο
append  πολιτιστικός_κληρονομιά
append  γεωργικός_έκταση
append  αγροτικό_τοπίο
append  γεωργικός_παραγωγή
append  οικονομικός_ανάπτυξη
append  τροφικός_αλυσίδα

NOT in vocabulary:  βιομηχανίος βιομηχανίος_ειδός_διατροφή
append  βιομηχανίος
append  βιομηχανίος_ειδός_διατροφή

NOT in vocabulary:  τροφίμα ποιότητας_τροφίμα
append  τροφίμα
append  ποιότητας_τροφίμα
append  επίδραση_φαινομένο_θερμοκηπίο
append  φαινόμενο_θερμοκηπίο
append  βιομηχανικός_ανάπτυξη
append  αγορά_εργασία
append  χερσαίος_πρόσβαση
--- only one word, not a new topic> αναδασμός
--- only one word, not a new topic> χωροταξία
append  αρχιτεκτονικός_τοπίο
append  σχεδιασμός_ανάπλαση_τοπίο
append  χρήση_γης
append  χωροταξικός_σχεδιασμός
append  θαλάσσιος_περιβάλλον
append  διατήρηση_φύση
append  προστασία_φύση
append

/home/dzon/kajo/kajo_semexp_core/lib/python3.6/site-packages/ipykernel_launcher.py:55: DeprecationWarning: elementwise comparison failed; this will raise an error in the future.
/home/dzon/kajo/kajo_semexp_core/lib/python3.6/site-packages/ipykernel_launcher.py:47: DeprecationWarning: elementwise comparison failed; this will raise an error in the future.


append  υδάτινη_μάζα
append  υδατικός_διάβρωση

NOT in vocabulary:  υδάτο διαχείριση_υδάτο
append  υδάτο
append  διαχείριση_υδάτο
append  αιολικός_διάβρωση
append  θαλάσσιος_οικοσύστημα
append  παράκτιος_οικοσύστημα

NOT in vocabulary:  ύδατο οικοσύστημα_γλυκά_ύδατο_γλυκέος_υδάτο
append  ύδατο

NOT in vocabulary:  γλυκέος οικοσύστημα_γλυκά_ύδατο_γλυκέος_υδάτο
append  γλυκέος

NOT in vocabulary:  υδάτο οικοσύστημα_γλυκά_ύδατο_γλυκέος_υδάτο
append  οικοσύστημα_γλυκά_ύδατο_γλυκέος_υδάτο
append  υδάτινος_οικοσύστημα
append  πλωτός_οδός
append  χωροταξικό_σχέδιο
append  εργατικό_δυναμικό

NOT in vocabulary:  πλωτέ εσωτερικός_πλωτέ_μεταφορή
append  πλωτέ
append  εσωτερικός_πλωτέ_μεταφορή
append  τιμή_αγρόκτημα
append  κλιματικός_μεταβολή
append  τεχνολογικός_μεταβολή
append  περιβαλλοντικός_μεταβολή
append  διαχείριση_σχεδιασμός_χρήση_γαία
append  ανάπτυξη_υδατικός_πόρο
append  βιομηχανικός_καλλιέργεια
append  διατήρηση_υδατικός_πόρο
--- only one word, not a new topic> αυτοκινητοβιομηχανία
a

append  φαρμακευτικός_βιομηχανία
append  διαβίωση_ζώο
append  διάρθρωση_πληθυσμός
append  πρόσβαση_θάλασσα
append  ορεινός_περιοχή
append  αστικό_τοπίο
append  νέος_εγκατάσταση
--- only one word, not a new topic> τουρισμό
append  αγροτικός_οικολογία
append  βιολογικός_παραγωγή
append  λίπανση_εδάφου
append  περιβαλλοντικός_ανάπτυξη
append  εδαφικός_πόροι
--- only one word, not a new topic> διαχείριση
--- only one word, not a new topic> πολιτική
append  δασικός_εκμετάλλευση
append  αποκατάσταση_γαία_εδάφου
append  συγκοινωνιακό_δίκτυο
append  αλατότητα_εδάφου
append  αλατότητα_ύδατος
append  αναπτυξιακός_σχεδιασμός
append  προγραμματισμός_συγκοινωνία
append  γεωργικός_εξοπλισμός

NOT in vocabulary:  εκτρεφόμενος εκτρεφόμενος_ζώο_αγροκτήματο
append  εκτρεφόμενος

NOT in vocabulary:  αγροκτήματο εκτρεφόμενος_ζώο_αγροκτήματο
append  αγροκτήματο
append  εκτρεφόμενος_ζώο_αγροκτήματο
append  νομοθεσία_νόμοι_σχετικά_βιομηχανία
append  οικονομικός_βοήθει
append  ποιότητας_περιβάλλον
append  υγρ

append  περιφερειακός_κανονισμός
append  περιβαλλοντικός_πολιτική
append  φυσικός_δρυμός

NOT in vocabulary:  βιομηχανίος βιομηχανίος_κλάδος_δέρμα
append  βιομηχανίος_κλάδος_δέρμα
append  καθαρισμός_διαμέσο_εδάφου
append  βελτίωση_εδάφου
append  θαλάσσιος_γεωλογία
append  σύστημα_προστασία
append  βιομηχανικός_διαδικασία_μέθοδοι
append  αποικοδόμηση_διάσπαση_ρύπο

NOT in vocabulary:  βιομηχανίος βιομηχανίος_παραγωγή_ενέργεια
append  βιομηχανίος_παραγωγή_ενέργεια
append  περιβαλλοντικός_βιομηχανία
--- only one word, not a new topic> αποστράγγιση
--- only one word, not a new topic> εισόδημα
append  προστασία_τοποθεσία
append  διαχείριση_ποταμός
--- only one word, not a new topic> άνεμος
append  δημόσιος_πληροφορία
append  εδαφικός_διαδικασία

NOT in vocabulary:  ύδατο ύδατο_επεξεργασία
append  ύδατο_επεξεργασία
--- only one word, not a new topic> ύδρευση
append  βιομηχανικός_περιοχή
append  χερσαίος_διάθεση
append  θερμότητα_όρο_φυσικός
append  οικολογικός_κοινότητα

NOT in vocabulary:  

...


NOT in vocabulary:  υπερχλωροαιθυλένιο υπερχλωροαιθυλένιο
append  υπερχλωροαιθυλένιο
--- only one word, not a new topic> υπερχλωροαιθυλένιο
--- only one word, not a new topic> αποτέφρωση
--- only one word, not a new topic> δοκιμασία
--- only one word, not a new topic> δεξαμενή
--- only one word, not a new topic> ακτινίδες
append  αναφορά_υπουργό
append  φορτίο_όχληση
--- only one word, not a new topic> αυτοκινητόδρομος

NOT in vocabulary:  άλατο δόμος_βύσμα_άλατο
append  δόμος_βύσμα_άλατο
append  δεξαμενή_καθίζηση_λάσπης
--- only one word, not a new topic> διοίκηση

NOT in vocabulary:  υπόλειμμας υπόλειμμας_αποτέφρωση
append  υπόλειμμας_αποτέφρωση
--- only one word, not a new topic> γαλακτωματοποίηση
append  αντιρρυπαντικός_πρωτοβουλία
--- only one word, not a new topic> φρέον
--- only one word, not a new topic> δοκιμασία
--- only one word, not a new topic> έγγραφο
--- only one word, not a new topic> κατασκήνωση
--- only one word, not a new topic> στρατόπεδο
--- only one word, not a n

--- only one word, not a new topic> αφομοίωση
--- only one word, not a new topic> βαφή
--- only one word, not a new topic> ανιχνευτής
--- only one word, not a new topic> κίνδυνοι

NOT in vocabulary:  φρύνοι φρύνοι
append  φρύνοι
--- only one word, not a new topic> φρύνοι
--- only one word, not a new topic> κάθαρση
append  επίσημη_ακρόαση
append  κάδος_απορριμμάτο
--- only one word, not a new topic> ύφασμα
append  συναίνεση_ενημέρωση

NOT in vocabulary:  halons απαγόρευση_cfc_halons
append  halons
append  απαγόρευση_cfc_halons
--- only one word, not a new topic> τοξικολογία
--- only one word, not a new topic> αντιδραστήρας

NOT in vocabulary:  απορρίμματας καύσιμο_απορρίμματας
append  καύσιμο_απορρίμματας
--- only one word, not a new topic> διαβούλευση

NOT in vocabulary:  υδατοφράκτης υδατοφράκτης
append  υδατοφράκτης
--- only one word, not a new topic> υδατοφράκτης
--- only one word, not a new topic> όπλο
append  πολιτικός_επιστήμη

NOT in vocabulary:  στοχευόμενος στοχευόμενος_οργανι


NOT in vocabulary:  κατηγορίο κατηγορίο_απειλούμενος_εξαφάνιση_είδου
append  κατηγορίο
append  κατηγορίο_απειλούμενος_εξαφάνιση_είδου
--- only one word, not a new topic> αντίσωμα

NOT in vocabulary:  διεργαστηριακός διεργαστηριακός_σύγκριση
append  διεργαστηριακός
append  διεργαστηριακός_σύγκριση
--- only one word, not a new topic> δείκτης
--- only one word, not a new topic> βάριο
append  καταλυτικός_μετατροπέας
--- only one word, not a new topic> φωτεινότητο
--- only one word, not a new topic> επώαση

NOT in vocabulary:  δνσο κώδικας_δνσο_διακυβερνητικός_ναυτιλιακός
append  δνσο
append  κώδικας_δνσο_διακυβερνητικός_ναυτιλιακός
append  διερεύνηση_τερατογένεση

NOT in vocabulary:  βρυόφυτα βρυόφυτα
--- only one word, not a new topic> βρυόφυτα
--- only one word, not a new topic> δόση

NOT in vocabulary:  συμπλοκοποίηση μέσος_συμπλοκοποίηση
append  συμπλοκοποίηση
append  μέσος_συμπλοκοποίηση

NOT in vocabulary:  αντιρρυπαντικό αντιρρυπαντικό_μέσο
append  αντιρρυπαντικό_μέσο
--- only one 

append  καύση_ελέγχο_πυρσό
--- only one word, not a new topic> αλκάνιο
--- only one word, not a new topic> προαγορά
--- only one word, not a new topic> πίδακας
--- only one word, not a new topic> μετάκαυση
--- only one word, not a new topic> καταλύτης
append  ορ_ρ_ός_γάλακτο
append  προωθητικό_μέσο
--- only one word, not a new topic> βιοφυσικός
--- only one word, not a new topic> κλάδευση

NOT in vocabulary:  γεωστοιχείο γεωστοιχείο_πληροφορία_αναφορά
append  γεωστοιχείο
append  γεωστοιχείο_πληροφορία_αναφορά
--- only one word, not a new topic> ναυτία
--- only one word, not a new topic> κάτοικος
append  μετατροπή_όζον
append  βαθμονόμηση_διακρίβωση
--- only one word, not a new topic> βοοειδή
--- only one word, not a new topic> ανταγωνισμό
--- only one word, not a new topic> ορμίσκος
append  ενημερωτικό_δελτίο
--- only one word, not a new topic> δίπτερα

NOT in vocabulary:  παλαιοκλιματολογία παλαιοκλιματολογία
append  παλαιοκλιματολογία
--- only one word, not a new topic> παλαιοκλιματο

append  καταστροφή_όζον

NOT in vocabulary:  απόβληα απόβληα_πάρκο
append  απόβληα_πάρκο
append  πλαίσιο_πολιτική
append  εφαρμογή_πολιτική

NOT in vocabulary:  πρωτογενής πρωτογενής_ενέργεια
append  πρωτογενής_ενέργεια

NOT in vocabulary:  αποτυπώματος μέθοδος_περιβαλλοντικός_αποτυπώματος_προϊόν
append  αποτυπώματος
append  μέθοδος_περιβαλλοντικός_αποτυπώματος_προϊόν

NOT in vocabulary:  παραγωγος παραγωγος_καταναλωτισμός
append  παραγωγος
append  παραγωγος_καταναλωτισμός
append  οδηγία_προώθηση_χρήση_ενέργεια_ανανεώσιμες_πηγή
append  παραγωγικότητα_πόρο
append  λεκάνη_απορροή_ποταμός
append  θόρυβος_οδικός_κυκλοφορία
append  στόχοι_βιώσιμη_ανάπτυξη

NOT in vocabulary:  αειφόρος αειφόρος_διαχείριση_δασής

NOT in vocabulary:  δασής αειφόρος_διαχείριση_δασής
append  αειφόρος_διαχείριση_δασής

NOT in vocabulary:  ύδατο μεταβατικά_ύδατο
append  μεταβατικά_ύδατο

NOT in vocabulary:  ύδατο οδηγία_πλαίσιο_ύδατο
append  οδηγία_πλαίσιο_ύδατο

NOT in vocabulary:  απορρίμματας οικιακά_απορρίμματ

In [29]:
get_vector('οραγανισμος')

[]

In [30]:
# add topics to model
model.add(new_words,new_vectors)

In [31]:
# save the model with new topics
model.save_word2vec_format(excluded_model_name, binary=True)
#reload the model  otherwise cannot find similarities fo newly added words
model = KeyedVectors.load_word2vec_format(excluded_model_name, binary=True)

In [34]:
len(model.index2word)

188506

In [32]:
# try the model
model.similar_by_vector('τροφικός_αλυσίδα')

[('αλυσίδα', 0.8525586128234863),
 ('τροφικός', 0.847536563873291),
 ('διαχείριση_αλυσίδα', 0.8260982632637024),
 ('τροφικός_παραγωγή_γεωργία', 0.7643824815750122),
 ('τροφικός_οικολογία', 0.7598724365234375),
 ('τροφικός_ανάγκα', 0.712148904800415),
 ('παραγωγή_πετρελαίος_αλυσίδα_παραγωγή', 0.6960781812667847),
 ('τροφική', 0.6921268701553345),
 ('ζωικός_τροφή', 0.6499475836753845),
 ('εφοδιαστικός', 0.6478005647659302)]

In [33]:
# find most similar to topics to terms in the new model

# load the new lemma list
with open(lemma_list_file_excluded) as fp:
    topics = fp.readlines()

for i, topic in enumerate(topics):
    topic = topic.strip()
    print('\n-----\n', topic)
    try:
        print(i, model.similar_by_vector(topic))
    except:
        print(topic, 'NOT in model')


-----
 τοπικός_ανάπτυξη
0 [('τοπικός', 0.9259339570999146), ('τοπικός_χρηματοδότηση', 0.9184502959251404), ('τοπικός_αυτοδιοίκηση', 0.9008185863494873), ('πολιτική_τοπικός_αυτοδιοίκηση', 0.8912954330444336), ('τοπικός_συγκοινωνία', 0.8760334849357605), ('περιφερειακός_ανάπτυξη', 0.8525574803352356), ('τοπικός_δάσωση', 0.8447407484054565), ('πολιτιστικός_ανάπτυξη', 0.8288854956626892), ('αρχός_οργανισμός_τοπικός_αυτοδιοίκηση', 0.8195730447769165), ('αγροτικός_ανάπτυξη', 0.8165229558944702)]

-----
 αγροτικός_ανάπτυξη
1 [('αγροτικός', 0.9061649441719055), ('αγροτικός_προγραμματισμός', 0.9037591218948364), ('αγροτικός_βιοτεχνολογία', 0.8781105279922485), ('αγροτικός_περιοχή', 0.8640522956848145), ('αγροτικός_γεωργικός_υποβάθμιση', 0.8631686568260193), ('διαχείριση_σχεδιασμός_αγροτικός_περιοχή', 0.855894923210144), ('βιομηχανικός_ανάπτυξη', 0.8445568084716797), ('ανάπτυξη', 0.8395471572875977), ('περιβαλλοντικός_ανάπτυξη', 0.8394483327865601), ('περιφερειακός_ανάπτυξη', 0.8393310308456421

20 [('αναδασώσεο', 0.6772181987762451), ('δασικός_εκμετάλλευση', 0.661196231842041), ('κτηματογράφηση', 0.6535839438438416), ('αγροτικός_οικισμός', 0.6516191959381104), ('αποψίλωση_δασικός_έκταση', 0.6489866375923157), ('δασικός_παραγωγή', 0.6467995643615723), ('διαχείριση_καλλιεργήσιμος_εκτάσεο', 0.6456829309463501), ('αρδευτικός_καλλιέργεια', 0.6395858526229858), ('δασικός_έκταση', 0.6392446756362915), ('δασικός_οικονομία', 0.6391103267669678)]

-----
 χωροταξία
21 [('χωροταξικός', 0.7094249725341797), ('χωροταξικός_σχεδιασμός', 0.6873317360877991), ('χωροταξικός_κινητικότητα', 0.6808292865753174), ('πολεοδομία', 0.6503422856330872), ('νομοθεσία_χωροταξία_πολεοδομία_χρήσεο_γης', 0.6442088484764099), ('αστικός_σχεδιασμός_ανάπτυξη', 0.6411310434341431), ('χωροταξικό', 0.6401455998420715), ('οικιστικός_σχεδιασμός', 0.6306002736091614), ('πολεοδομικός_πολιτική', 0.6272222995758057), ('αγροτικός_οικολογία', 0.6211225986480713)]

-----
 αρχιτεκτονικός_τοπίο
22 [('τοπίο', 0.9685208797454834

44 [('υδατικός', 0.8730529546737671), ('χημικός_διάβρωση', 0.8192143440246582), ('διάβρωση', 0.817745566368103), ('αιολικός_διάβρωση', 0.8139599561691284), ('προστασία_διάβρωση', 0.806133508682251), ('διατήρηση_υδατικός_πόρο', 0.7711890339851379), ('περιοχή_προστασία_υδατικός_πόρο', 0.7693510055541992), ('ανάπτυξη_υδατικός_πόρο', 0.7548831105232239), ('διαχείριση_υδατικός_πόρο', 0.7515442371368408), ('διατήρηση_γλυκός_υδατικός_πόρο', 0.7434683442115784)]

-----
 διαχείριση_υδάτο
45 [('διαχείριση_επιφανειακός_υδάτο', 0.9790865182876587), ('παρακολούθηση_υδάτο', 0.9743796586990356), ('διαχείριση_ποιότητα_υδάτο', 0.9706845283508301), ('υδάτος', 0.9689470529556274), ('υδάτο', 0.9689470529556274), ('επαναχρησιμοποίηση_υδάτο', 0.9688280820846558), ('αξιοποίηση_υδάτο', 0.9658952951431274), ('προστασία_υδάτο', 0.9621844291687012), ('δημοτικός_διαχείριση_υδάτο', 0.9482517242431641), ('διαχείριση_ποσότητα_υδάτο', 0.9378798007965088)]

-----
 αιολικός_διάβρωση
46 [('αιολικός', 0.8272441625595093)

65 [('διαχείριση_υδάτο', 0.9706845283508301), ('διαχείριση_επιφανειακός_υδάτο', 0.962097704410553), ('βελτίωση_ποιότητα_υδάτο', 0.9574434757232666), ('διαχείριση_ποσότητα_υδάτο', 0.947490930557251), ('προστασία_υδάτο', 0.9409512877464294), ('αξιοποίηση_υδάτο', 0.9376593828201294), ('παρακολούθηση_υδάτο', 0.9362053871154785), ('ποιότητας_υδάτο', 0.9328067302703857), ('επαναχρησιμοποίηση_υδάτο', 0.9327395558357239), ('δημοτικός_διαχείριση_υδάτο', 0.9292328953742981)]

-----
 καλλιέργεια_γεωργικός_έκταση
66 [('γεωργικός_έκταση', 0.9760689735412598), ('δασικός_έκταση', 0.8607709407806396), ('δασικός_έκταση_εύκρατη_περιοχή', 0.8508135080337524), ('έκταση', 0.8333170413970947), ('αποψίλωση_δασικός_έκταση', 0.8307339549064636), ('αλκαλικός_έκταση', 0.8285630941390991), ('λιβαδικός_έκταση_διάσπαρτος_αλσύλλιο', 0.8140884041786194), ('ξηρικός_καλλιέργεια', 0.7945184707641602), ('χερσαίος_έκταση', 0.7880258560180664), ('γεωργικός_εκμετάλλευση', 0.7873971462249756)]

-----
 γεωργικός_πολιτική
67 [

87 [('κοινωνικός', 0.8808444738388062), ('κοινωνικός_διαδικασία', 0.8778276443481445), ('κοινωνικός_προστασία', 0.8550190925598145), ('κοινωνικός_πολιτική', 0.8520681858062744), ('κοινωνικός_ανάπτυξη', 0.8507267236709595), ('κοινωνικός_ασφάλεια', 0.841333270072937), ('υγειονομικός_υπηρεσία', 0.8391848802566528), ('οικοσυστημικός_υπηρεσία', 0.8364627361297607), ('υπηρεσία', 0.8343413472175598), ('κοινωνικός_συμπεριφορά', 0.8239780068397522)]

-----
 φυσικός_πόροι
88 [('βιολογικός_πόροι', 0.9579724073410034), ('μικροβιολογικός_πόροι', 0.9484622478485107), ('ενεργειακός_πόροι', 0.9475435614585876), ('φυτικός_πόροι', 0.9415897130966187), ('πόροι', 0.9389151334762573), ('γενετικός_πόροι', 0.9333329200744629), ('κλιματικός_πόροι', 0.9329137802124023), ('ανανεώσιμοι_πόροι', 0.9323215484619141), ('υδατικός_πόροι', 0.9321975708007812), ('ανανεώσιμος_πόροι', 0.9280207753181458)]

-----
 δασικός_πόροι
89 [('εδαφικός_πόροι', 0.9141544103622437), ('βιολογικός_πόροι', 0.9131688475608826), ('φυτικός_

...

4980 [('δράση', 0.8864776492118835), ('ομάδα_δράση', 0.826080322265625), ('πρόγραμμα', 0.8112419843673706), ('οδηγία_πλαισίο_κοινοτικός_δράση_πλαίσιο_πολιτική_θαλάσσιος_περιβάλλον', 0.8007259368896484), ('πρόγραμμα_πλαίσιο_γεωργία', 0.7591623663902283), ('περιβαλλοντικό_πρόγραμμα', 0.7501813173294067), ('πρόγραμμα_αυτοβοήθεια', 0.7369117736816406), ('οικονομικό_πρόγραμμα_σχέδιο', 0.7327792048454285), ('πρόγραμμα_ανάλυση', 0.7158730030059814), ('περιβάλλον', 0.7093801498413086)]

-----
 περιβαλλοντικό_αποτύπωμα
4981 [('οικολογικό_αποτύπωμα', 0.9360263347625732), ('αποτύπωμα', 0.9186983704566956), ('περιβαλλοντικό', 0.7726632356643677), ('περιβαλλοντικό_πρόγραμμα', 0.7151198983192444), ('περιβαλλοντικό_κόστος', 0.6943597793579102), ('περιβαλλοντικό_χρηματιστήριο', 0.6925444602966309), ('περιβαλλοντικό_κριτήριο', 0.6915838718414307), ('αποτύπωµα', 0.6856116056442261), ('περιβαλλοντικό_σχέδιο', 0.6640628576278687), ('περιβαλλοντικό_δίκαιο', 0.6574691534042358)]

-----
 περιβαλλοντικός_διακ


-----
 εκπομπός_αερία_θερμοκηπίο
4998 [('πολιτικός_αερία_διαπραγματεύσει_εκπομπός', 0.8764771819114685), ('αερία', 0.8586668372154236), ('καθαρισμός_αερία', 0.8169330954551697), ('εκπομπή_απαερίων_καυσαερίο', 0.779843807220459), ('εκπομπός_ατμόσφαιρα', 0.779126763343811), ('επεξεργασίας_αερία', 0.7686118483543396), ('θερμοκηπίο', 0.7568297386169434), ('αέριο_προκαλώ_φαινόμενο_θερμοκηπίο', 0.7481551170349121), ('καλλιέργεια_θερμοκηπίο', 0.7420599460601807), ('εκπομπός_καυσαερίο_κυκλοφορίο_αυτοκινήτο', 0.7296841740608215)]

-----
 υπέργειος_βιομάζα
4999 [('βιομάζα', 0.8690646886825562), ('υπόγεια_βιομάζα', 0.8527880907058716), ('ενέργεια_βιομάζα', 0.8426473140716553), ('ανάπτυξη_υπόγειας_βιομάζα', 0.7517272233963013), ('υπέργειος', 0.6945297718048096), ('ζωικός_κοπριά_καύσιμο', 0.6628756523132324), ('φυτομάζας', 0.6570595502853394), ('γεωθερμικός_ενέργεια', 0.647294282913208), ('βιοκαύσιμο', 0.6328216791152954), ('υπέργει', 0.6208568811416626)]

-----
 οδηγία_οικοτόπου
5000 [('οδηγία', 

5024 [('πόρο', 0.9348124861717224), ('διαχείριση_πόρο', 0.9088971614837646), ('εκμετάλλευση_πόρο', 0.90263831615448), ('πολιτική_διατίμηση_πόρο', 0.8185151815414429), ('ανάπτυξη_υδατικός_πόρο', 0.8110983371734619), ('διαχείριση_φυσικός_πόρο', 0.8003278970718384), ('διαχείριση_υδατικός_πόρο', 0.786636471748352), ('υποβάθμιση_φυσικός_πόρο', 0.7710715532302856), ('διατήρηση_θαλάσσιος_πόρο', 0.76478511095047), ('χρήση_πόρο', 0.7645047307014465)]

-----
 λεκάνη_απορροή_ποταμός
5025 [('λεκάνη_απορροή', 0.9299801588058472), ('ανάπτυξη_ποτάμια_λεκάνη', 0.8725305795669556), ('προστατευόμενη_περιοχή_εκβολή_ποταμός_ποταμόκολπο', 0.8552845120429993), ('διαχείριση_λεκάνης_απορροή', 0.8541853427886963), ('εκβολή_ποταμός', 0.84555983543396), ('υδρογραφικός_λεκάνη', 0.8379172086715698), ('κοίτη_ποταμός', 0.8283330202102661), ('λεκάνη', 0.8244950771331787), ('διαχείριση_ποταμός', 0.823650598526001), ('προστασία_λεκάνης_απορροή_υδάτο', 0.8121110200881958)]

-----
 θόρυβος_οδικός_κυκλοφορία
5026 [('οδικό

5044 [('οικοτοξικολογικός', 0.7998293042182922), ('τοξικολογία', 0.7906690239906311), ('οικοτοξικότητο', 0.7651761770248413), ('τοξικολογικός', 0.7357192039489746), ('τοξικολογικά', 0.6958023309707642), ('οικοτοξικολογικός_αξιολόγηση', 0.6718016266822815), ('φυτοτοξικότηα', 0.6543248295783997), ('τοξικολογικός_αξιολόγηση', 0.6499338150024414), ('γονοτοξικότηα', 0.6119427680969238), ('περιβαλλοντικός_χημεία', 0.6004723310470581)]

-----
 μύκητε
5045 [('μύκητα', 0.9295316338539124), ('ζυμομύκητα', 0.774337887763977), ('μικροοργανισμού', 0.6372899413108826), ('βακτήριο', 0.6154047846794128), ('μύκητας', 0.5991032123565674), ('μυκητα', 0.5944863557815552), ('μυκήτο', 0.5898927450180054), ('βακτηρίδιο', 0.5857629776000977), ('μυκητιάσει', 0.5849075317382812), ('μυκητίαση', 0.5832557082176208)]

-----
 ορνιθόμορφο
5046 [('στρουθιόμορφα', 0.6739031076431274), ('στρουθιόμορφο', 0.6117671728134155), ('στρουθιόμορφας', 0.6071373820304871), ('θηλαστικός', 0.598491907119751), ('αιλουροειδός', 0.59

5064 [('απογραφός', 0.9999999403953552), ('απογραφή_πληθυσμός', 0.8998123407363892), ('οικολογικός_απογραφή', 0.8722355961799622), ('απογραφικός', 0.8335704803466797), ('απογραφικά', 0.7545815706253052), ('απογραφη', 0.7070258259773254), ('απογραφέας', 0.6973709464073181), ('απογραφώ', 0.6865010261535645), ('απογραφικό', 0.6813549399375916), ('απογράφηκαν', 0.6667767763137817)]

-----
 βιοηθικός
5065 [('ιατρικός_επιστήμη', 0.6381776332855225), ('επιστημονικός_οικολογία', 0.6165607571601868), ('περιβαλλοντικός_ιατρικός', 0.6066358685493469), ('νομικός_επιστήμη', 0.5993152856826782), ('διεπιστημονικός', 0.5984050631523132), ('περιβαλλοντικός_δεοντολογία', 0.5903937816619873), ('ανθρώπινη_βιολογία', 0.5880486965179443), ('βιοϊατρικός', 0.5862998962402344), ('ανοσία_ιατρικός', 0.5836668610572815), ('επιστημολογία', 0.5833785533905029)]

-----
 τραχειόφυτα
5066 [('βρυόφυτα', 0.790231466293335), ('πτεριδόφυτα', 0.787940502166748), ('ανθόφυτα', 0.6817355155944824), ('σαπρόφυτα', 0.61581492424